### Iniciando SparkSession

In [0]:
from pyspark.sql import SparkSession

# Create a SparkSession with the required configurations for Delta Lake
spark = SparkSession.builder \
    .appName("Leitura Delta") \
    .config("spark.sql.extensions", "io.delta.sql.DeltaSparkSessionExtension") \
    .config("spark.sql.catalog.spark_catalog", "org.apache.spark.sql.delta.catalog.DeltaCatalog") \
    .getOrCreate()

#### Número de Núcleos

In [0]:
num_cores = sc._jsc.sc().getExecutorMemoryStatus().keySet().size()
print(f"Número de núcleos no cluster: {num_cores}")


Número de núcleos no cluster: 1


####Evidência de Fato Vendas

In [0]:
from delta.tables import DeltaTable
delta_path = "dbfs:/mnt/lhdw/gold/vendas_delta"
delta_table = DeltaTable.forPath(spark, f"{delta_path}/fato_vendas")
delta_table.toDF().show()

+----------+----------+------------+-----------+-------------+-----------+--------+-------------+-------------+-----------+----+---+----------------+
| DataVenda|sk_produto|sk_categoria|sk_segmento|sk_fabricante| sk_cliente|Unidades|PrecoUnitario|CustoUnitario|TotalVendas| Ano|Mes|data_atualizacao|
+----------+----------+------------+-----------+-------------+-----------+--------+-------------+-------------+-----------+----+---+----------------+
|2011-03-18|        33|           2|          8|            1|42949674427|       1|        88.19|        64.38|      88.19|2011|  3|            null|
|2011-03-26|        33|           2|          8|            1| 8589938563|       1|        88.19|        64.38|      88.19|2011|  3|            null|
|2011-03-19|        33|           2|          8|            1|25769807991|       1|        88.19|        64.38|      88.19|2011|  3|            null|
|2011-03-21|        33|           2|          8|            1| 8589936048|       1|        88.19|   

####Evidência de Dim Produto

In [0]:
from delta.tables import DeltaTable
delta_path = "dbfs:/mnt/lhdw/gold/vendas_delta"
dim_produto_df = DeltaTable.forPath(spark, f"{delta_path}/dim_produto")
dim_produto_df.toDF().show()

+---------+-------------+---------+----------+--------------------+
|IDProduto|      Produto|Categoria|sk_produto|    data_atualizacao|
+---------+-------------+---------+----------+--------------------+
|      585|Maximus UC-50|    Urban|         1|2024-10-01 17:17:...|
|      555|Maximus UC-20|      Mix|         2|2024-10-01 17:17:...|
|      423|Maximus UM-28|    Urban|         3|2024-10-01 17:17:...|
|      681|Maximus UC-46|    Urban|         4|2024-10-01 17:17:...|
|      628|Maximus UC-93|    Urban|         5|2024-10-01 17:17:...|
|      415|Maximus UM-20|    Urban|         6|2024-10-01 17:17:...|
|      547|Maximus UC-12|      Mix|         7|2024-10-01 17:17:...|
|      653|Maximus UC-18|    Urban|         8|2024-10-01 17:17:...|
|      512|Maximus UR-01|    Urban|         9|2024-10-01 17:17:...|
|      520|Maximus UE-08|    Urban|        10|2024-10-01 17:17:...|
|      609|Maximus UC-74|    Urban|        11|2024-10-01 17:17:...|
|      471|Maximus UM-76|    Urban|        12|20

####Evidência de Dim Geografia

In [0]:
from delta.tables import DeltaTable
delta_path = "dbfs:/mnt/lhdw/gold/vendas_delta"
dim_geografia_df = DeltaTable.forPath(spark, f"{delta_path}/dim_geografia")
dim_geografia_df.toDF().show()

+-------------+------+-------+------------+----+------------+------------+--------------------+
|       Cidade|Estado| Regiao|    Distrito|Pais|CodigoPostal|sk_geografia|    data_atualizacao|
+-------------+------+-------+------------+----+------------+------------+--------------------+
|   Mount Dora|    FL|   East|District #12| USA|       32757|           1|2024-10-01 17:18:...|
|   Chesapeake|    VA|   East|District #07| USA|       23323|           2|2024-10-01 17:18:...|
|     Big Rock|    VA|   East|District #19| USA|       24603|           3|2024-10-01 17:18:...|
| Jacksonville|    FL|   East|District #12| USA|       32225|           4|2024-10-01 17:18:...|
|  Los Angeles|    CA|   West|District #37| USA|       90003|           5|2024-10-01 17:18:...|
|        Paris|    KY|   East|District #16| USA|       40361|           6|2024-10-01 17:18:...|
|Milledgeville|    GA|   East|District #09| USA|       31061|           7|2024-10-01 17:18:...|
|      Creston|    IL|Central|District #

####Evidência de Dim Categoria

In [0]:
from delta.tables import DeltaTable
delta_path = "dbfs:/mnt/lhdw/gold/vendas_delta"
dim_categoria_df = DeltaTable.forPath(spark, f"{delta_path}/dim_categoria")
dim_categoria_df.toDF().show()


+---------+------------+--------------------+
|Categoria|sk_categoria|    data_atualizacao|
+---------+------------+--------------------+
|      Mix|           1|2024-10-01 17:17:...|
|    Urban|           2|2024-10-01 17:17:...|
|    Youth|           3|2024-10-01 17:17:...|
|Accessory|           4|2024-10-01 17:17:...|
|    Rural|           5|2024-10-01 17:17:...|
+---------+------------+--------------------+



####Evidência de Dim Cliente

In [0]:
from pyspark.sql.functions import *
from delta.tables import DeltaTable
delta_path = "dbfs:/mnt/lhdw/gold/vendas_delta"
#dim_cliente_df = DeltaTable.forPath(spark, f"{delta_path}/dim_cliente")
dim_cliente_df = spark.read.format("delta").load(delta_path+"/dim_cliente")
# Conte o número de linhas
#dim_cliente_df.count()
display(dim_cliente_df)


IDCliente Nome Email sk_geografia sk_cliente data_atualizacao 96376 Sheila Taylor sheila.taylor@xyza.com 1683 1 2024-10-01T17:18:49.334+0000 84148 Winifred Cash winifred.cash@xyza.com 8589937566 2 2024-10-01T17:18:49.334+0000 80484 Kessie Frank kessie.frank@xyza.com 8589938667 3 2024-10-01T17:18:49.334+0000 67819 Maggie Odonnell maggie.odonnell@xyza.com 1054 4 2024-10-01T17:18:49.334+0000 26074 Darius William darius.william@xyza.com 8589937383 5 2024-10-01T17:18:49.334+0000 65581 Giacomo Dudley giacomo.dudley@xyza.com 8589936797 6 2024-10-01T17:18:49.334+0000 251276 Yolanda Schroeder yolanda.schroeder@xyza.com 8589940176 7 2024-10-01T17:18:49.334+0000 185513 Caleb Gillespie caleb.gillespie@xyza.com 8589937327 8 2024-10-01T17:18:49.334+0000 170611 Meghan Kane meghan.kane@xyza.com 8589938816 9 2024-10-01T17:18:49.334+0000 11067 Ava Carter ava.carter@xyza.com 8589936728 10 2024-10-01T17:18:49.334+0000 1205 Zahir Leblanc zahir.leblanc@xyza.com 8589942623 11 2024-10-01T17:18:49.334+0000 80417 Ainsley Salazar ainsley.salazar@xyza.com 2352 12 2024-10-01T17:18:49.334+0000 191433 Dylan Joseph dylan.joseph@xyza.com 2347 13 2024-10-01T17:18:49.334+0000 185958 Herman Clark herman.clark@xyza.com 8589934732 14 2024-10-01T17:18:49.334+0000 110009 Brynn Mann brynn.mann@xyza.com 8589935492 15 2024-10-01T17:18:49.334+0000 98242 Bert Galloway bert.galloway@xyza.com 8589935902 16 2024-10-01T17:18:49.334+0000 255519 Portia Sloan portia.sloan@xyza.com 8589935372 17 2024-10-01T17:18:49.334+0000 183704 Imelda Adkins imelda.adkins@xyza.com 2111 18 2024-10-01T17:18:49.334+0000 37834 Baker Mathis baker.mathis@xyza.com 1005 19 2024-10-01T17:18:49.334+0000 114396 Zenaida Clay zenaida.clay@xyza.com 4135 20 2024-10-01T17:18:49.334+0000 87383 Taylor Washington taylor.washington@xyza.com 3227 21 2024-10-01T17:18:49.334+0000 209580 Carlos Stuart carlos.stuart@xyza.com 1432 22 2024-10-01T17:18:49.334+0000 162952 Rana Garrett rana.garrett@xyza.com 8589939259 23 2024-10-01T17:18:49.334+0000 117858 Driscoll Coffey driscoll.coffey@xyza.com 8589939862 24 2024-10-01T17:18:49.334+0000 50357 Lee William lee.william@xyza.com 5086 25 2024-10-01T17:18:49.334+0000 177808 Driscoll Richardson driscoll.richardson@xyza.com 8589938136 26 2024-10-01T17:18:49.334+0000 233527 James Oneil james.oneil@xyza.com 247 27 2024-10-01T17:18:49.334+0000 105155 Raphael Kelly raphael.kelly@xyza.com 1697 28 2024-10-01T17:18:49.334+0000 249320 Lucas Dejesus lucas.dejesus@xyza.com 8589935298 29 2024-10-01T17:18:49.334+0000 278109 Maggie Bates maggie.bates@xyza.com 8589940965 30 2024-10-01T17:18:49.334+0000 243371 Daria Romero daria.romero@xyza.com 8589934755 31 2024-10-01T17:18:49.334+0000 236705 Rina Bernard rina.bernard@xyza.com 4947 32 2024-10-01T17:18:49.334+0000 199290 Beverly Jensen beverly.jensen@xyza.com 8589937273 33 2024-10-01T17:18:49.334+0000 10974 Leilani Nicholson leilani.nicholson@xyza.com 8589941514 34 2024-10-01T17:18:49.334+0000 149829 Barclay Knapp barclay.knapp@xyza.com 8589940000 35 2024-10-01T17:18:49.334+0000 264853 Kaitlin Wells kaitlin.wells@xyza.com 8589938217 36 2024-10-01T17:18:49.334+0000 234634 MacKensie Wise mackensie.wise@xyza.com 8589940901 37 2024-10-01T17:18:49.334+0000 145686 Abdul Kline abdul.kline@xyza.com 4527 38 2024-10-01T17:18:49.334+0000 203960 Summer Rogers summer.rogers@xyza.com 8589934695 39 2024-10-01T17:18:49.334+0000 192748 Fiona Rollins fiona.rollins@xyza.com 4666 40 2024-10-01T17:18:49.334+0000 7329 Brynn Young brynn.young@xyza.com 8589938206 41 2024-10-01T17:18:49.334+0000 228966 Giacomo Contreras giacomo.contreras@xyza.com 4470 42 2024-10-01T17:18:49.334+0000 267008 Clinton Rutledge clinton.rutledge@xyza.com 8589940718 43 2024-10-01T17:18:49.334+0000 234375 Camilla Kirkland camilla.kirkland@xyza.com 5304 44 2024-10-01T17:18:49.334+0000 145095 Brent Wolf brent.wolf@xyza.com 1507 45 2024-10-01T17:18:49.334+0000 191479 Kato Alvarez kato.alvarez@xyza.com 8589940429 46 2024-10-01T17:18:49.334+0000 275522 Mallory Underwood mallory.underwood@xyza.com

####Evidência de Dim Fabricante

In [0]:
from delta.tables import DeltaTable
delta_path = "dbfs:/mnt/lhdw/gold/vendas_delta"
dim_fabricante_df = DeltaTable.forPath(spark, f"{delta_path}/dim_fabricante")
dim_fabricante_df.toDF().show()

+------------+----------+-------------+--------------------+
|IDFabricante|Fabricante|sk_fabricante|    data_atualizacao|
+------------+----------+-------------+--------------------+
|           7| VanArsdel|            1|2024-10-01 17:18:...|
+------------+----------+-------------+--------------------+



####Evidência de Dim Segmento

In [0]:
from delta.tables import DeltaTable
delta_path = "dbfs:/mnt/lhdw/gold/vendas_delta"
dim_segmento_df = DeltaTable.forPath(spark, f"{delta_path}/dim_segmento")
dim_segmento_df.toDF().show()

+------------+-----------+--------------------+
|    Segmento|sk_segmento|    data_atualizacao|
+------------+-----------+--------------------+
|  All Season|          1|2024-10-01 17:18:...|
|     Extreme|          2|2024-10-01 17:18:...|
|       Youth|          3|2024-10-01 17:18:...|
|Productivity|          4|2024-10-01 17:18:...|
|     Regular|          5|2024-10-01 17:18:...|
| Convenience|          6|2024-10-01 17:18:...|
|  Moderation|          7|2024-10-01 17:18:...|
|   Accessory|          8|2024-10-01 17:18:...|
|      Select|          9|2024-10-01 17:18:...|
+------------+-----------+--------------------+



%md
**Dicas para Otimizar a Performance**
> **Particionamento**: Definimos partições adequadas para evitar leituras desnecessárias e melhorar a performance de consultas.

> **Codec de compressão**: Usamos Snappy, pois oferece boa performance de compressão e descompressão.

> **Shuffle partitions**: Definimos um valor fixo para spark.sql.shuffle.partitions para melhorar o paralelismo durante operações como joins e agregações.
> Além disso, podemos explorar técnicas como cache para tabelas pequenas (dimensões) que são frequentemente acessadas, e broadcast join para otimizar joins entre a tabela Fato e as tabelas de dimensões

### Otimização de Leitura com predicate pushdown:
- Certifique-se de que as consultas estão aproveitando o predicate pushdown, o que significa que os filtros são aplicados diretamente ao ler os dados, melhorando a eficiência.


In [0]:
# Utilizando predicate pushdown para otimizar a consulta
# Caminho para o diretório dos arquivos Delta
gold_path = "dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas"
df_filtrado = spark.read.format("delta").load(gold_path).filter("Ano = 2012 AND Mes = 10")

display(df_filtrado)

DataVenda sk_produto sk_categoria sk_segmento sk_fabricante sk_cliente Unidades PrecoUnitario CustoUnitario TotalVendas Ano Mes data_atualizacao 2012-10-17 19 2 6 1 60129550649 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-31 19 2 6 1 7385 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-24 19 2 6 1 25769809950 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-24 19 2 6 1 5173 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-17 19 2 6 1 6151 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-04 19 2 6 1 17179875796 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-11 19 2 6 1 25769809581 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-08 19 2 6 1 60129548380 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-26 19 2 6 1 60129550137 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-15 19 2 6 1 34359744122 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-14 19 2 6 1 7386 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-07 19 2 6 1 51539613979 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-08 19 2 6 1 17179874805 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-13 19 2 6 1 34359743724 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-31 19 2 6 1 5302 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-25 19 2 6 1 25769809456 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-10 19 2 6 1 6769 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-23 19 2 6 1 34359743134 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-14 19 2 6 1 6991 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-04 19 2 6 1 51539614087 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-11 19 2 6 1 34359743606 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-25 19 2 6 1 5551 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-10 19 2 6 1 42949679966 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-24 19 2 6 1 8589940897 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-10 19 2 6 1 25769808824 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-11 19 2 6 1 25769804843 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-29 19 2 6 1 34359746012 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-08 19 2 6 1 60129550650 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-24 19 2 6 1 42949679718 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-13 19 2 6 1 17179875167 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-26 19 2 6 1 5686 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-15 19 2 6 1 25769811361 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-31 19 2 6 1 5919 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-16 19 2 6 1 17179875797 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-11 19 2 6 1 8589940503 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-20 19 2 6 1 25769811486 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-18 19 2 6 1 25769810069 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-18 19 2 6 1 8589941750 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-05 19 2 6 1 60129548524 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-15 19 2 6 1 51539612519 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-26 19 2 6 1 51539614186 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-27 19 2 6 1 5056 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-12 19 2 6 1 8589942034 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-15 19 2 6 1 60129549152 1 36.74 26.82 36.74 2012 10 2024-10-01T17:24:04.244+0000 2012-10-19 19 2 6 1 

#### Broadcast join
**Explicação:**
**1. Broadcast Join:**

- O broadcast() é aplicado às tabelas de <b>dimensões</b> (dim_produto_df e dim_cliente_df). Isso replica as tabelas de dimensão para todos os nós, permitindo que as junções sejam realizadas localmente em cada nó, sem necessidade de comunicação entre nós, o que melhora a performance em clusters distribuídos.

**2. Junção com Broadcast:**

- As junções são feitas entre as colunas de chave original (IDProduto, IDCliente) e as tabelas de dimensão para obter as chaves substitutas (SK_Produto, SK_Cliente).

**3. Particionamento:**

- Adicionamos colunas de Ano e Mês para otimizar o armazenamento da tabela de fatos e melhorar o desempenho em consultas temporais. A tabela é particionada por essas colunas.

**Vantagens do Broadcast Join:**

- Reduz a movimentação de dados durante a operação de junção, pois as dimensões pequenas são replicadas para todos os nós.
- Aumenta a performance quando as tabelas de dimensão são significativamente menores que a tabela de fatos, o que é o caso comum em arquiteturas de data warehouse.

**Desvantagens do Broadcast Join:**
- Limitação de Memória: O DataFrame menor deve caber na memória de todos os nós. Se o DataFrame for muito grande, pode causar erros de falta de memória

In [0]:
from pyspark.sql.functions import year, sum, broadcast,desc
from pyspark.sql import SparkSession

# Leitura das tabelas Delta
vendas_df = spark.read.format("delta").load("/mnt/lhdw/gold/vendas_delta/fato_vendas")
categoria_df = spark.read.format("delta").load("/mnt/lhdw/gold/vendas_delta/dim_categoria")

# Usar broadcast para a tabela categoria
 
categoria_df = broadcast(categoria_df)

# Realizar o join entre as tabelas
joined_df = vendas_df.join(categoria_df, vendas_df.sk_categoria == categoria_df.sk_categoria)

# Agrupar por categoria e ano e calcular a soma do total de vendas
resultado_df = joined_df.groupBy("Categoria", "Ano")\
        .agg(sum("TotalVendas").alias("TotalVendas"))\
        .orderBy("Ano",desc("TotalVendas"))


display(resultado_df)

Categoria Ano TotalVendas Urban 2011 8852821.620001657 Accessory 2011 872290.7399999888 Mix 2011 790909.2799999828 Youth 2011 77043.70999999945 Rural 2011 2132.7799999999997 Urban 2012 9517020.880001487 Accessory 2012 1022819.599999977 Mix 2012 667064.9999999995 Youth 2012 192043.06999999855 Rural 2012 164.06

**Melhorias de Performance**

Filtros de Partição: Se você souber quais partições específicas deseja ler, aplicar filtros nas partições pode reduzir significativamente o tempo de leitura.
Reparticionamento: Se os dados estiverem distribuídos de forma desigual, você pode usar repartition() para redistribuir o DataFrame com base em uma coluna-chave.

# Dicas de Performance com PySpark

## 1. Use DataFrame/Dataset em vez de RDD
Os DataFrames e Datasets são mais eficientes que os RDDs, pois incluem otimizações automáticas e um motor de execução otimizado. Eles permitem um melhor gerenciamento de memória e execução mais rápida.

## 2. Evite UDFs (User Defined Functions)
As UDFs podem ser lentas porque não são otimizadas pelo Catalyst Optimizer do Spark. Sempre que possível, use as funções internas do Spark SQL, que são mais eficientes.

## 3. Use `coalesce()` em vez de `repartition()`
O `coalesce()` é mais eficiente que o `repartition()` para reduzir o número de partições, pois evita o shuffle de dados.

## 4. Cache de Dados
Cache os DataFrames que são reutilizados várias vezes em suas operações. Isso evita a re-leitura dos dados do disco e melhora o desempenho.

## 5. Reduza Operações de Shuffle
Operações de shuffle, como `groupByKey` e `reduceByKey`, podem ser caras. Use `mapPartitions` e `reduceByKey` sempre que possível para minimizar o shuffle.

## 6. Ajuste o Número de Partições
Ajuste o número de partições para equilibrar a carga de trabalho entre os executores. Um número inadequado de partições pode levar a um uso ineficiente dos recursos.

## 7. Use Formatos de Dados Serializados
Formatos de dados como Parquet e ORC são mais eficientes para leitura e escrita, pois são compactados e otimizados para consultas.

## 8. Ajuste as Configurações do Spark
Ajuste configurações como `spark.executor.memory`, `spark.executor.cores` e `spark.sql.shuffle.partitions` para otimizar o uso de recursos.

## 9. Utilize a Adaptive Query Execution (AQE)
A AQE permite que o Spark ajuste dinamicamente o plano de execução das consultas com base nas estatísticas de tempo de execução, melhorando o desempenho.

Implementar essas práticas pode ajudar a melhorar significativamente o desempenho de suas aplicações PySpark. Se precisar de mais detalhes ou tiver outras perguntas, estou aqui para ajudar! 🤜🤛